# Imports

In [1]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings import OpenAIEmbeddings
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.chat_models import ChatOpenAI
from langchain.document_loaders import PyPDFDirectoryLoader
import plotly.express as px
from langchain.vectorstores.redis import Redis
import requests
import umap
from dotenv import load_dotenv
import os
import torch
from torch import cuda
import transformers

/home/justin/.local/lib/python3.10/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/justin/.local/lib/python3.10/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/justin/.local/lib/python3.10/site-packages/umap/distances.py:1086: NumbaDeprecationWarning: Th

# Load ENV variables & Set Model Variables

In [2]:
load_dotenv()
hf_token = os.getenv('HFTOKEN')
API_KEY = os.getenv("OPENAI_API_KEY")
org_id = os.getenv("ORG_ID")
model_id = 'meta-llama/Llama-2-7b-chat-hf'
embed_model_id = 'sentence-transformers/all-MiniLM-L6-v2'
device = f'cuda:{cuda.current_device()}' if cuda.is_available() else 'cpu'

# Loading Documents

In [3]:
dirpath = "dataset"

In [4]:
loader = PyPDFDirectoryLoader(dirpath)
data = loader.load()

In [5]:
data

[Document(page_content='2021\nNVIDIA CORPORATION  \nANNUAL REVIEW\nNOTICE OF ANNUAL MEETING\nPROXY STATEMENT \nFORM 10-K', metadata={'source': 'dataset/2021-Annual-Review.pdf', 'page': 0}),
 Document(page_content='“AMERICA’S  \nMOST IMPORTANT  \nCOMPANY ”\nFORBES\nThis was a year that none of us will forget. \nBut extraordinary companies rise in extraordinary \ntimes. We are building a once-in-a-generation \ncompany to tackle the world’s greatest \nchallenges —one that made these extraordinary \ntimes into one of our finest hours.\nJensen Huang', metadata={'source': 'dataset/2021-Annual-Review.pdf', 'page': 1}),
 Document(page_content='', metadata={'source': 'dataset/2021-Annual-Review.pdf', 'page': 2}),
 Document(page_content='“WE’RE SEEING A MAJOR  \nCHANGE IN HOW WE THINK OF  \nPC GRAPHICS, AND IT SHOULDN’T  \nBE A SURPRISE THAT NVIDIA IS \nLEADING THE WAY ”\nTECH RADAR\nGaming is the world’s largest entertainment \nindustry. With more than 200 million gamers, \nNVIDIA GeForce is it

# Chunking

In [6]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=2000, chunk_overlap=200)

In [7]:
docs=text_splitter.split_documents(data)

In [8]:
len(docs)

1712

# Model

In [9]:
# # begin initializing HF items, need auth token for these
# model_config = transformers.AutoConfig.from_pretrained(
#     model_id,
#     use_auth_token=hf_token
# )

# model = transformers.AutoModelForCausalLM.from_pretrained(
#     model_id,
#     trust_remote_code=True,
#     config=model_config,
#     torch_dtype=torch.float16,
#     device_map='auto',
#     use_auth_token=hf_token
# )
# model.eval()
# print(f"Model loaded on {device}")



In [10]:
# tokenizer = transformers.AutoTokenizer.from_pretrained(
#     embed_model_id,
#     use_auth_token=hf_token
# )

# generate_text = transformers.pipeline(
#     model=model, tokenizer=tokenizer,
#     return_full_text=True,  # langchain expects the full text
#     task='text-generation',
#     # we pass model parameters here too
#     temperature=0.1,  # 'randomness' of outputs, 0.0 is the min and 1.0 the max
#     max_new_tokens=512,  # mex number of tokens to generate in the output
#     repetition_penalty=1.1  # without this output begins repeating
# )


# res = generate_text("Explain to me the difference between llama 2 and gpt.")
# print(res[0]["generated_text"])

Lamma 2 took too long for inference and the local resources that I have is not practical to use such a large model as such openai will be used

In [11]:
llm = ChatOpenAI(model_name="gpt-3.5-turbo", temperature=0,openai_api_key=API_KEY, openai_organization=org_id)

# Embeddings

In [12]:
# embed_model = HuggingFaceEmbeddings(
#     model_name=embed_model_id,
#     model_kwargs={'device': device},
#     encode_kwargs={'device': device, 'batch_size': 32}
# )

In [13]:
embeddings = OpenAIEmbeddings(openai_api_key=API_KEY)

In [14]:
texts = [d.page_content for d in docs]
metadatas = [d.metadata for d in docs]

In [15]:
texts

['2021\nNVIDIA CORPORATION  \nANNUAL REVIEW\nNOTICE OF ANNUAL MEETING\nPROXY STATEMENT \nFORM 10-K',
 '“AMERICA’S  \nMOST IMPORTANT  \nCOMPANY ”\nFORBES\nThis was a year that none of us will forget. \nBut extraordinary companies rise in extraordinary \ntimes. We are building a once-in-a-generation \ncompany to tackle the world’s greatest \nchallenges —one that made these extraordinary \ntimes into one of our finest hours.\nJensen Huang',
 '“WE’RE SEEING A MAJOR  \nCHANGE IN HOW WE THINK OF  \nPC GRAPHICS, AND IT SHOULDN’T  \nBE A SURPRISE THAT NVIDIA IS \nLEADING THE WAY ”\nTECH RADAR\nGaming is the world’s largest entertainment \nindustry. With more than 200 million gamers, \nNVIDIA GeForce is its largest platform. GeForce \nRTX GPUs and the GeForce Experience \napplication transform everyday PCs into \npowerful gaming machines.\nPowered by the NVIDIA Ampere architecture —\nour 2nd-gen RTX design, GeForce RTX 30 Series \nGPUs deliver incredibly realistic ray-traced \ngraphics and cutt

In [16]:
metadatas

[{'source': 'dataset/2021-Annual-Review.pdf', 'page': 0},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 1},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 3},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 5},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 6},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 7},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 8},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 9},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 10},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 11},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 12},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 13},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 13},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 13},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 14},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 14},
 {'source': 'dataset/2021-Annual-Review.pdf', 'page': 14},
 {'so

# Run Redis Server using the official image

```docker run -it --rm --name redis-stack    -p 6379:6379    redis/redis-stack:latest```

# Set up Vector Store

In [18]:
rds, keys = Redis.from_texts_return_keys(
    texts, embeddings, redis_url="redis://localhost:6400", index_name="source"
)

# Query from Vector Store

In [19]:
query = "How did Nvidia perform for Environmental, Social, and Governance (ESG) these couple of years"
results = rds.similarity_search(query,k=50)

In [20]:
results

[Document(page_content='Environmental, Social and Corporate Governance\nNVIDIA invents computing technologies that improve lives and address global challenges. We integrate sound \nenvironmental, social and corporate governance, or ESG, principles and practices into every aspect of the Company. The \nNominating and Corporate Governance Committee of our Board of Directors is responsible for reviewing and discussing \nwith management our practices concerning ESG. We undertake an annual analysis to ensure that our ESG priorities \nremain aligned with stakeholder expectations, market trends, and business risks and opportunities. These issues are \nimportant for our continued business success and reflect the topics of highest concern to NVIDIA and our stakeholders. \nThe following section provides an overview of some of these principles and practices. More information can be found on \nthe Corporate Social Responsibility section of our website and in our annual Corporate Social Responsibili

# Visualising Retrieval Results

In [21]:
import pandas as pd

In [22]:
df = pd.DataFrame([{'page_content': doc.page_content} for doc in results])
sentences = []
for d in df['page_content']:
    sentences.append(str(d))

In [23]:
pd.set_option('display.max_colwidth', None)
print(df)

In [24]:
sentences = []
for d in df['page_content']:
    sentences.append(str(d))

In [25]:
sentences

['Environmental, Social and Corporate Governance\nNVIDIA invents computing technologies that improve lives and address global challenges. We integrate sound \nenvironmental, social and corporate governance, or ESG, principles and practices into every aspect of the Company. The \nNominating and Corporate Governance Committee of our Board of Directors is responsible for reviewing and discussing \nwith management our practices concerning ESG. We undertake an annual analysis to ensure that our ESG priorities \nremain aligned with stakeholder expectations, market trends, and business risks and opportunities. These issues are \nimportant for our continued business success and reflect the topics of highest concern to NVIDIA and our stakeholders. \nThe following section provides an overview of some of these principles and practices. More information can be found on \nthe Corporate Social Responsibility section of our website and in our annual Corporate Social Responsibility Report, or \nCSR Re

In [26]:
model_id = "sentence-transformers/all-MiniLM-L6-v2"
api_url = f"https://api-inference.huggingface.co/pipeline/feature-extraction/{model_id}"
headers = {"Authorization": f"Bearer {hf_token}"}
def query(texts):
    response = requests.post(api_url, headers=headers, json={"inputs": texts, "options":{"wait_for_model":True}})
    return response.json()
output = query(sentences)

In [27]:
def umap_plot(text, emb):

    cols = list(text.columns)
    # UMAP reduces the dimensions from 1024 to 2 dimensions that we can plot
    reducer = umap.UMAP(n_neighbors=2)
    umap_embeds = reducer.fit_transform(emb)
    # Prepare the data to plot and interactive visualization
    # using Altair
    #df_explore = pd.DataFrame(data={'text': qa['text']})
    #print(df_explore)
    
    #df_explore = pd.DataFrame(data={'text': qa_df[0]})
    df_explore = text.copy()
    df_explore['x'] = umap_embeds[:,0]
    df_explore['y'] = umap_embeds[:,1]
    
    # Plot
    df_explore['text'] = text['page_content'].str[:50]  # Assuming 'text' is a column in your original DataFrame
    
    fig = px.scatter(df_explore, x='x', y='y', color='text', title='UMAP Visualization')
    fig.update_traces(marker=dict(size=10, opacity=0.8))
    fig.update_layout(width=800, height=500, hovermode='closest',legend=dict(x=1, y=1))
    fig.show()
  
    return 

In [28]:
chart = umap_plot(df, output)

/home/justin/.local/lib/python3.10/site-packages/numba/np/ufunc/parallel.py:371: NumbaWarning: The TBB threading layer requires TBB version 2021 update 6 or later i.e., TBB_INTERFACE_VERSION >= 12060. Found TBB_INTERFACE_VERSION = 12050. The TBB threading layer is disabled.
  warnings.warn(problem)


In [29]:
from langchain.prompts.prompt import PromptTemplate
from langchain.memory import ConversationBufferMemory

In [46]:
custom_template = """Based on the chat history and documents, answer the following question. If the documents does not make sense try to follow up the question with the chat history. If you don't know do not output false information but highlight that you don't know.
Chat History:
{chat_history}
Follow Up Input: {question}
Documents: {docs}
Standalone question:"""

In [57]:
CUSTOM_QUESTION_PROMPT = PromptTemplate.from_template(custom_template)

In [50]:
memory = ConversationBufferMemory(memory_key="chat_history", return_messages=True)

In [58]:
query = "How did Nvidia perform for Environmental, Social, and Governance (ESG) these couple of years"

In [62]:
from langchain.agents.agent_toolkits import create_retriever_tool

retriever = rds.as_retriever(k= 3)

tool = create_retriever_tool(
    retriever, 
    'doc_retrieve',
    'this retrives the docs'
)

tools = [tool]

from langchain.agents.openai_functions_agent.agent_token_buffer_memory import AgentTokenBufferMemory

memory_key = "history"
memory = AgentTokenBufferMemory(memory_key=memory_key, llm=llm)

from langchain.agents.openai_functions_agent.base import OpenAIFunctionsAgent
from langchain.schema.messages import SystemMessage
from langchain.prompts import MessagesPlaceholder

system_message = SystemMessage(
        content=(
            "Do your best to answer the questions. "
            "Feel free to use any tools available to look up "
            "relevant information, only if neccessary"
        )
)

prompt = OpenAIFunctionsAgent.create_prompt(
        system_message=system_message,
        extra_prompt_messages=[MessagesPlaceholder(variable_name=memory_key)]
    )

agent = OpenAIFunctionsAgent(llm=llm, tools=tools, prompt=prompt)

from langchain.agents import AgentExecutor

agent_executor = AgentExecutor(agent=agent, tools=tools, memory=memory, verbose=True,
                                   return_intermediate_steps=True)

result = agent_executor({"input": query})
result



> Entering new AgentExecutor chain...

Invoking: `doc_retrieve` with `Nvidia ESG performance`


[Document(page_content='Environmental, Social and Corporate Governance\nNVIDIA invents computing technologies that improve lives and address global challenges. We integrate sound \nenvironmental, social and corporate governance, or ESG, principles and practices into every aspect of the Company. The \nNominating and Corporate Governance Committee of our Board of Directors is responsible for reviewing and discussing \nwith management our practices concerning ESG. We undertake an annual analysis to ensure that our ESG priorities \nremain aligned with stakeholder expectations, market trends, and business risks and opportunities. These issues are \nimportant for our continued business success and reflect the topics of highest concern to NVIDIA and our stakeholders. \nThe following section provides an overview of some of these principles and practices. More information can be found on \nthe Corp

{'input': 'How did Nvidia perform for Environmental, Social, and Governance (ESG) these couple of years',
 'history': [HumanMessage(content='How did Nvidia perform for Environmental, Social, and Governance (ESG) these couple of years', additional_kwargs={}, example=False),
  AIMessage(content='', additional_kwargs={'function_call': {'name': 'doc_retrieve', 'arguments': '{\n  "__arg1": "Nvidia ESG performance"\n}'}}, example=False),
  FunctionMessage(content="[Document(page_content='Environmental, Social and Corporate Governance\\nNVIDIA invents computing technologies that improve lives and address global challenges. We integrate sound \\nenvironmental, social and corporate governance, or ESG, principles and practices into every aspect of the Company. The \\nNominating and Corporate Governance Committee of our Board of Directors is responsible for reviewing and discussing \\nwith management our practices concerning ESG. We undertake an annual analysis to ensure that our ESG priorities \

In [65]:
print(result['output'])

Nvidia integrates sound Environmental, Social, and Corporate Governance (ESG) principles and practices into every aspect of the company. The Nominating and Corporate Governance Committee of the Board of Directors is responsible for reviewing and discussing Nvidia's practices concerning ESG. They undertake an annual analysis to ensure that their ESG priorities remain aligned with stakeholder expectations, market trends, and business risks and opportunities.

In terms of environmental impact, Nvidia addresses climate impacts across its product lifecycle and assesses risks, including current and emerging regulations and market impacts. They report several metrics related to their environmental impact in their Corporate Social Responsibility (CSR) Report. The most recent full reporting year is fiscal year 2021, and the fiscal year 2022 metrics are expected to be published in May 2022. There has been no material impact to capital expenditures, results of operations, or competitive position 

In [66]:
query='Do you think that your previous answer affects the earnings'
result = agent_executor({"input": query})
print(result['output'])



> Entering new AgentExecutor chain...
As an AI language model, I don't have access to real-time financial data or the ability to predict the impact of ESG performance on a company's earnings. ESG performance can have various effects on a company's financial performance, including potential benefits such as improved brand reputation, increased customer loyalty, and access to sustainable investment opportunities. However, the specific impact on earnings would depend on various factors, including the industry, market conditions, and the extent to which ESG practices are integrated into the company's operations and strategy. It would be best to consult financial analysts or refer to Nvidia's financial reports for a comprehensive understanding of their earnings and the potential impact of ESG performance.

> Finished chain.
As an AI language model, I don't have access to real-time financial data or the ability to predict the impact of ESG performance on a company's earnings. ESG performan

In [67]:
query='what are the earnings of nvidia across the years'
result = agent_executor({"input": query})
print(result['output'])



> Entering new AgentExecutor chain...

Invoking: `doc_retrieve` with `Nvidia annual earnings`


[Document(page_content='NVIDIA had an excellent year. Full-year \nrevenue was a record $26.91 billion, up \n61 percent from $16.68 billion a year ago. \nGross margins expanded to 64.9 percent, \nand earnings per share were $3.85, up \n123 percent from a year ago. We \nreturned $399 million during the year  \nto shareholders through quarterly  \ncash dividends.\nOur top priority remains the continued \nexpansion of NVIDIA accelerated \ncomputing—creating software, systems, \nand chips to serve new markets. NVIDIA \ngrows through any combination of these. \nNew chips open new markets. For \nexample, the new Orin robotics \nprocessor chip is the central computer \nfor a new generation of logistics robots, \ndelivery robots, and self-driving cars, \ntrucks, and taxis. And Grace is a new \nCPU architecture designed for ultra-fast \ndata processing, the essential operation \nof AI and machine le

In [68]:
query='so which year did they improved their earnings the most'
result = agent_executor({"input": query})
print(result['output'])



> Entering new AgentExecutor chain...
Nvidia experienced significant improvement in their earnings in Fiscal Year 2022 compared to the previous year. Here are the key changes in earnings between the two fiscal years:

- Revenue: Increased by 61% from $16.68 billion in the previous year to a record $26.91 billion in Fiscal Year 2022.
- Gross Margin: Expanded to 64.9% in Fiscal Year 2022, representing an increase of 260 basis points compared to the previous year.
- Operating Income: Increased by 122% from the previous year to $10.0 billion in Fiscal Year 2022.
- Diluted Earnings Per Share (EPS): Rose by 123% from the previous year to $3.85 in Fiscal Year 2022.

Based on these figures, it can be concluded that Nvidia's earnings improved the most in Fiscal Year 2022 compared to the previous year.

> Finished chain.
Nvidia experienced significant improvement in their earnings in Fiscal Year 2022 compared to the previous year. Here are the key changes in earnings between the two fiscal yea

In [69]:
query='hi my name is bob'
result = agent_executor({"input": query})
print(result['output'])



> Entering new AgentExecutor chain...
Hello Bob! How can I assist you today?

> Finished chain.
Hello Bob! How can I assist you today?


In [70]:
query='what is my name'
result = agent_executor({"input": query})
print(result['output'])



> Entering new AgentExecutor chain...
Your name is Bob.

> Finished chain.
Your name is Bob.
